## Zephyr-7B
Source:

- https://huggingface.co/HuggingFaceH4/zephyr-7b-beta
- https://huggingface.co/spaces/HuggingFaceH4/zephyr-chat
- https://arxiv.org/abs/2310.16944

### Setup

In [1]:
%pip install -U openai

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.0/77.0 KB 1.1 MB/s eta 0:00:00 MB/s eta 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.3/78.3 KB 2.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.6/62.6 KB 1.5 MB/s eta 0:00:000:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 6.4 MB/s eta 0:00:00m eta 0:00:010:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 142.1/142.1 KB 4.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 124.2/124.2 KB 2.8 MB/s eta 0:00:00m eta 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.5/61.5 KB 9.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 158.3/158.3 KB 4.2 MB/s eta 0:00:0031m29.8 MB/s eta 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.2/61.2 KB 1.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 KB 3.7 MB/s eta 0:00:00m eta 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 225.7/225.7 KB 3.7 MB/s eta 0:00:00m eta 0:00:01
     ━━━━━

In [5]:
%pip show openai

Name: openai
Version: 0.28.1
Summary: Python client library for the OpenAI API
Home-page: https://github.com/openai/openai-python
Author: OpenAI
Author-email: support@openai.com
License: 
Location: /home/limcheekin/ws/py/openllm-function-calling/venv/lib/python3.10/site-packages
Requires: aiohttp, requests, tqdm
Required-by: 
Note: you may need to restart the kernel to use updated packages.


In [23]:
import openai
import os

openai.api_key  = os.getenv('HF_API_KEY')
openai.api_base = "https://limcheekin-zephyr-7b-beta-gguf.hf.space/v1"


### Prompt Format
```
<|system|>
</s>
<|user|>
{prompt}</s>
<|assistant|>
```
---
```
<|system|>
You are a friendly chatbot who always responds in the style of a pirate.</s>
<|user|>
How many helicopters can a human eat in one sitting?</s>
<|assistant|>
Ah, me hearty matey! But yer question be a puzzler! A human cannot eat a helicopter in one sitting, as helicopters are not edible. They be made of metal, plastic, and other materials, not food!
```

In [24]:
def get_prompt(system_prompt: str, instruction: str):
    prompt = f"<|system|>\n{system_prompt}</s>\n<|user|>\n{instruction}</s>\n<|assistant|>\n"
    return prompt

In [25]:
print(get_prompt(system_prompt="You are a helpful assistant.", instruction="Tell me more about yourself."))

<|system|>
You are a helpful assistant.</s>
<|user|>
Tell me more about yourself.</s>
<|assistant|>



### Completion Function

In [26]:
import time

DEFAULT_SYSTEM_PROMPT = "You are a helpful assistant, you will complete the task by follow the instructions given."

# Source: https://platform.openai.com/docs/api-reference/completions/create
def get_completion(prompt, system_prompt=DEFAULT_SYSTEM_PROMPT, temperature=0.0, max_tokens=512):
    prompt = get_prompt(system_prompt=system_prompt, instruction=prompt)
    start_time = time.time()
    response = openai.Completion.create(
        model="",
        prompt=prompt,
        temperature=temperature, 
        max_tokens=max_tokens,
        request_timeout=600,
        stream=True
    )
    return combine_chunks(start_time, response)

# Source: https://github.com/openai/openai-cookbook/blob/main/examples/How_to_stream_completions.ipynb
def combine_chunks(start_time, response):
    # create variables to collect the stream of chunks
    collected_messages = []
    # iterate through the stream of events
    for chunk in response:
        chunk_time = time.time() - start_time  # calculate the time delay of the chunk
        chunk_message = chunk['choices'][0]['text']  # extract the message
        collected_messages.append(chunk_message)  # save the message
        print(chunk_message, end='')
        # print(f"Message received {chunk_time:.2f} seconds after request: {chunk_message}")  # print the delay and text

    # print the time delay and text received
    print(f"\nResponse time taken: {chunk_time:.2f}s")
    full_reply_content = ''.join(collected_messages)
    return full_reply_content    

In [27]:
text = "What is AI?"
response = get_completion(text)

AI stands for Artificial Intelligence. It refers to the development of computer systems that can perform tasks that typically require human intelligence, such as learning, reasoning, and decision-making. These systems are designed to operate autonomously or with minimal human intervention, using techniques like machine learning, natural language processing, and neural networks. The goal of AI is to create intelligent machines that can help us solve complex problems, make better decisions, and improve our quality of life in various ways.
Response time taken: 30.80s
